### Conjugate Gradient: the Krylov subspace method for Quadratic Optimization $\def\b#1{\boldsymbol{ #1}}\def\B#1{\boldsymbol{ #1}}$

Conjugate gradient can be thought of as a Krylov subspace method for the quadratic optimization problem $\min(f(\b x)$ where
$$f(\b x)= \frac{1}{2}\b x^T\b A \b x + \b c^T \b x$$
and $\b A$ is symmetric positive definite (this makes the problem convex).

In this demo, we compare the result of conjugate gradient to an explicitly constructed Krylov subspace.

We start by picking a random $\b A$ and $\b c$:

In [1]:
import numpy as np
import numpy.linalg as la
import scipy.optimize as sopt

n = 32
# make A a random SPD matrix
Q = la.qr(np.random.randn(n, n))[0]
A = Q @ (np.diag(np.random.rand(n)) @ Q.T)

c = np.random.randn(n)

# pick number of steps of CG to execute
k = 10

# define quadratic objective function
def f(x):
    return .5*np.inner(x, A @ x) + np.inner(c,x)

/home/edgar/envs/py35env/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/home/edgar/envs/py35env/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


### Quadratic Programming using Arnoldi

First, we form a Krylov subspace using Arnoldi iteration on $\b A$ with starting guess $\b c$, then select the minima via
$$\B x_k = -||\B c||_2\B Q_k \B T_k^{-1} \B e_1 ,$$
which is a minimizer within this Krylov subspace since
\begin{align*}
\min_{\B x \in \mathcal{K}_k(\B A, \B c)} f(\B x) &= \min_{\B y \in \mathbb{R}^k} f(\B Q_k \B y)  \\
&=\min_{\B y \in \mathbb{R}^k} \B y^T \B Q_k^T \B A \B Q_k \B y + \B c^T \B Q_k \B y \\
&= \min_{\B y \in \mathbb{R}^k} \B y^T \B T_k \B y + ||\B c||_2\B e_1^T \B y.
\end{align*}


In [2]:
# initialize Krylov subspace, taking first column as c/||c||_2
Q = np.zeros((n,k))
T = np.zeros((k,k))
x_kr = np.zeros((n,k))
Q[:,0] = c / la.norm(c)

for i in range(1,k+1):
    # perform Lanczos iteration
    u = A @ Q[:,i-1]
    for j in range(0,i):
        T[j,i-1] = np.inner(Q[:,j],u)
        u = u - T[j,i-1]*Q[:,j]
    if i<k:
        T[i,i-1] = la.norm(u)
        Q[:,i] = u/T[i,i-1]
    # compute and store new best minimizer of f(x)
    if i>0:
        # compute approximate minima x_kr as -||\b c||_2\b Q \b T^{-1} \b e_1
        e1 = np.zeros(i) 
        e1[0] = la.norm(c)
        x_kr[:,i-1] = - Q[:,:i] @ la.solve(T[:i,:i],e1)
        print(f(x_kr[:,i-1]), "= min_{ x_kr in Krylov subspace of dimension ", i,"} f(x_kr)")

-14.883319154561752 = min_{ x_kr in Krylov subspace of dimension  1 } f(x_kr)
-17.424436343147732 = min_{ x_kr in Krylov subspace of dimension  2 } f(x_kr)
-17.72739276073426 = min_{ x_kr in Krylov subspace of dimension  3 } f(x_kr)
-17.785971326808593 = min_{ x_kr in Krylov subspace of dimension  4 } f(x_kr)
-17.800250205047668 = min_{ x_kr in Krylov subspace of dimension  5 } f(x_kr)
-17.80190450919875 = min_{ x_kr in Krylov subspace of dimension  6 } f(x_kr)
-17.802224995751303 = min_{ x_kr in Krylov subspace of dimension  7 } f(x_kr)
-17.8022517275579 = min_{ x_kr in Krylov subspace of dimension  8 } f(x_kr)
-17.80225428329917 = min_{ x_kr in Krylov subspace of dimension  9 } f(x_kr)
-17.80225465775456 = min_{ x_kr in Krylov subspace of dimension  10 } f(x_kr)


### Nonlinear Programming using Parallel Tangents for Quadratic Objective

Next, we implement Conjugate Gradient using the parallel tangents method, which is general to arbitrary nonlinear objective functions (but the convergence and optimality properties are only true for a convex quadratic objective function).

The parallel tangent method performs two line minimizations at each iteration:
  * Perform a step of steepest descent to generate $\B{\hat{x}}_{k}$ from $\B x_k$.
  * Generate $\B x_{k+1}$ by minimizing over the line passing through $\B x_{k-1}$ and $\B{\hat{x}}_{k}$.

To initialize the parallel tangents method, we use the two first approximate minima obtained from the Krylov subspace method above. Subsequent iterates are then reproduced exactly!

In [3]:
# perform conjugate gradient by parallel tangents method
x_cg_pp = np.zeros((n, k))
x_cg_pp[:,0] = x_kr[:,0]
x_cg_pp[:,1] = x_kr[:,1]

# perform CG method via parallel tangents method
for i in range(2,k):
    x = x_cg_pp[:,i-1]

    # define function for steepest descent, based on current iterate x and grad_f(x)
    # can use local variables within function
    def f_1d(a):
        return f(x + a*(A@x+c))

    # solve for best steepest descent step using golden section search and form x_hat
    a = sopt.golden(f_1d)
    x_hat = x + a * (A@x+c)

    # define function for extrapolation, based on last iterate x_cg_pp[:,i-2] and x_hat (the solution of steepest descent)
    # can use local variables within function
    def g_1d(a):
        return f(x_hat + a*(x_hat - x_cg_pp[:,i-2]))
    # solve for best extrapolation using golden section search and update x
    a = sopt.golden(g_1d)
    x = x_hat + a*(x_hat - x_cg_pp[:,i-2])

    # store CG iterate as next column of x_cg_pp
    x_cg_pp[:,i] = x
    print(f(x), " = f( conjugate gradient parallel tangents iterate", i, ")")

-17.72739276073426  = f( conjugate gradient parallel tangents iterate 2 )
-17.7859713268086  = f( conjugate gradient parallel tangents iterate 3 )
-17.80025020504766  = f( conjugate gradient parallel tangents iterate 4 )
-17.801904509198746  = f( conjugate gradient parallel tangents iterate 5 )
-17.80222499575131  = f( conjugate gradient parallel tangents iterate 6 )
-17.802251727557902  = f( conjugate gradient parallel tangents iterate 7 )
-17.802254283299174  = f( conjugate gradient parallel tangents iterate 8 )
-17.802254657754546  = f( conjugate gradient parallel tangents iterate 9 )


### Quadratic Programming by Conjugate Gradient

The 1D line minimizations in the parallel tangents method can be solved analytically given a quadratic objective, so the parallel tangents implementation can be transformed to use a couple of matrix vector products in place of the two golden section searches.

In [4]:
# perform CG method via matrix-vector products
x_cg_mv = np.zeros((n, k))
x_cg_mv[:,0] = x_kr[:,0]
x_cg_mv[:,1] = x_kr[:,1]

# this implementation mimics parallel tangents implementation,
# one of the matrix vector products can in fact be avoided
for i in range(2,k):
    x = x_cg_mv[:,i-1]

    # compute gradient
    g = A@x + c

    # compute explicit equation for optimal step size for steepest descent
    a = - np.inner(g,g)/np.inner(g, A@g)

    # update x
    x_hat = x + a * g

    # determine new optimization direction
    d = x_hat - x_cg_mv[:,i-2]

    # compute explicit equation for optimal step size in direction d = x_hat - x_{k-1}
    a = - np.inner(g,d)/np.inner(d, A@d)

    #update x
    x = x_hat + a * d

    # store CG iterate as next column of x_cg_mv
    x_cg_mv[:,i] = x
    print(f(x), " = f( conjugate gradient matrix vector product iterate", i, ")")

-17.72739276073426  = f( conjugate gradient matrix vector product iterate 2 )
-17.785971326808593  = f( conjugate gradient matrix vector product iterate 3 )
-17.800250205047668  = f( conjugate gradient matrix vector product iterate 4 )
-17.801904509198742  = f( conjugate gradient matrix vector product iterate 5 )
-17.8022249957513  = f( conjugate gradient matrix vector product iterate 6 )
-17.802251727557902  = f( conjugate gradient matrix vector product iterate 7 )
-17.802254283299167  = f( conjugate gradient matrix vector product iterate 8 )
-17.80225465775455  = f( conjugate gradient matrix vector product iterate 9 )


It can be shown that each step of Conjugate gradient causes an update $\b s_k = \b x_{k+1} - \b x_k$ that is $\b A$-conjugate ($\b A$-orthogonal) to the previous, i.e. $\b s_i^T\b A \b s_{i-1}$:

In [5]:
for i in range(2,k):
    print(np.inner(x_cg_mv[:,i]-x_cg_mv[:,i-1],A @ (x_cg_mv[:,i-1]-x_cg_mv[:,i-2])))

-4.996003610813204e-16
1.734723475976807e-17
-3.0010716134398763e-16
6.732895491134983e-17
-2.6684925970299478e-17
1.2187110045094873e-17
-3.085317510373789e-19
-9.91928520793989e-19


In fact $\b s_i^T \b A \b s_j= 0$ if $i\neq j$.

In [6]:
print((x_cg_mv[:,1:]-x_cg_mv[:,:-1]).T @ A @ (x_cg_mv[:,1:]-x_cg_mv[:,:-1]))

[[ 5.08223438e+00 -4.33631109e-16 -5.37064335e-16  3.54803518e-16
   2.45464518e-17  1.18677436e-15 -1.62780588e-15  1.86027526e-16
  -4.27305286e-16]
 [-3.09894433e-16  6.05912835e-01  3.03948429e-17  8.45870782e-19
  -2.25463235e-16 -1.40491749e-16  4.16221290e-16 -5.62387694e-16
   6.45241018e-16]
 [-6.10143315e-16  8.95144290e-18  1.17157132e-01 -3.03396421e-16
   1.88080315e-16  9.55441136e-17 -1.12769667e-16  1.46485092e-16
  -3.07589477e-16]
 [ 3.10956848e-16  8.70093097e-18 -2.96887933e-16  2.85577565e-02
   6.72074568e-17  7.10050037e-17 -4.78887108e-17 -5.18409712e-17
   8.34892991e-17]
 [ 2.37233635e-17 -2.31258883e-16  1.88392870e-16  6.72057643e-17
   3.30860830e-03 -2.65761972e-17  1.77677613e-17  1.58967570e-17
  -1.88536630e-17]
 [ 1.18886759e-15 -1.39933328e-16  9.48236325e-17  7.08862262e-17
  -2.67655804e-17  6.40973105e-04  1.21534006e-17 -1.96046260e-17
   1.78573525e-17]
 [-1.62739252e-15  4.16833317e-16 -1.12788355e-16 -4.78043788e-17
   1.77705059e-17  1.2163029

This fact permits a further optimization of the conjugate gradient iteration, resulting in only 1 matrx-vector product (the resulting work-efficient method can be found in many textbooks, papers, and on wikipedia).